# A brief introduction to nonlinear programming

## 1 Unconstrained optimization

### Task 1

In [1]:
import numpy as np

def f1(x):
    x1, x2 = x[0], x[1]
    return x1**2 + x2**2 - 2*x1*x2

def f2(x):
    x1, x2 = x[0], x[1]
    return 10*(x2-x1**2)**2 + (1-x1)**2

def f3(x):
    return np.dot(x, x) * 0.5

def oracle_f1(x, mode=2):
    x1, x2 = x[0], x[1]
    if mode == 1:
        return f1(x)
    if mode == 3:
        g = np.array([2*x1 - 2*x2, 2*x2 - 2*x1])
        return g
    if mode == 2:
        f = f1(x)
        g = np.array([2*x1 - 2*x2, 2*x2 - 2*x1])
        return f, g

def oracle_f2(x, mode=2):
    x1, x2 = x[0], x[1]
    if mode == 1:
        return f2(x)
    if mode == 3:
        g = np.array([-40*x1*(x2-x1**2) - 2*(1-x1),
                      20*(x2-x1**2)])
        return g
    if mode == 2:
        f = f2(x)
        g = np.array([-40*x1*(x2-x1**2) - 2*(1-x1),
                      20*(x2-x1**2)])
        return f, g

def oracle_f3(x, mode=2):
    if mode == 1:
        return f3(x)
    if mode == 3:
        g = x.copy()
        return g
    if mode == 2:
        f = f3(x)
        g = x.copy()
        return f, g


In [2]:
oracle_f1(np.array([np.array([25.0,4.0]), np.array([1.0,1.0])]))

(array([576.,   9.]),
 array([[ 48.,   6.],
        [-48.,  -6.]]))

### Task 2

In [3]:
def gradient_method(oracle, x0, step_size=0.01, max_iter=1000, tol=1e-6):
    x = np.array(x0, dtype=float)
    history = [x.copy()]
    for i in range(max_iter):
        f, g = oracle(x)
        # print("f", f, "x", x, "g", g)
        x_new = x - step_size * g
        history.append(x_new.copy())
        if np.linalg.norm(g) < tol:
            break
        x = x_new
    return x,history
    print(f,g)

# gradient_method(oracle_f2, np.array([np.array([25.0,4.0]), np.array([1.0,1.0])]), step_size=0.6)
# gradient_method(oracle_f1, [-2,2], step_size=0.05)

In [ ]:
(x2,h2)= gradient_method(oracle_f1, [-2,2], step_size=0.5)
print("step size 0.5:", x2, "iterations:", len(h2))
(x1,h1)= gradient_method(oracle_f1, [-2,2], step_size=0.05)
print("step size 0.05:", x1, "iterations:", len(h1))
(x3,h3)= gradient_method(oracle_f1, [-2,2], step_size=0.005)
print("step size 0.005:", x3, "iterations:", len(h3))

print("step size 0.5 fait du ping pong (valeur limite avant divergence, cf plots ci-dessous), et 0,005 converge mais plus lentement car trop petit")



step size 0.5: [-2.  2.] iterations: 1001
step size 0.05: [-1.68499667e-07  1.68499667e-07] iterations: 75
step size 0.005: [-1.76520379e-07  1.76520379e-07] iterations: 806
step size 0.5 fait du ping pong (au dessus ça diverge, cf plots ci-dessous), et 0,005 converge mais plus lentement car trop petit


In [11]:
import plotly.graph_objects as go
import plotly.offline as pyo
from plotly.subplots import make_subplots
import numpy as np

# Enable plotly offline mode for Jupyter
pyo.init_notebook_mode(connected=True)

def plot_convergence_3d_plotly(oracle, x0=[-2, 2], step_size=0.05,
                              x_range=(-3, 3), y_range=(-3, 3), grid_size=50, 
                              max_iter=1000, tol=1e-6):
    
    # Create grid for surface plot
    x1 = np.linspace(x_range[0], x_range[1], grid_size)
    x2 = np.linspace(y_range[0], y_range[1], grid_size)
    X1, X2 = np.meshgrid(x1, x2)
    
    # Evaluate function on grid
    Z = np.zeros_like(X1)
    for i in range(grid_size):
        for j in range(grid_size):
            point = np.array([X1[i,j], X2[i,j]])
            f_val = oracle(point, mode=1)
            Z[i,j] = f_val
    
    # Run gradient method to get convergence history
    x_opt, history = gradient_method(oracle, x0, step_size=step_size, max_iter=max_iter, tol=tol)
    
    # Extract path coordinates and function values
    path_x1 = [point[0] for point in history]
    path_x2 = [point[1] for point in history]
    path_z = []
    for point in history:
        f_val = oracle(point, mode=1)
        path_z.append(f_val)
    
    # Create plotly figure
    fig = go.Figure()
    
    # Add surface
    fig.add_trace(go.Surface(
        x=X1, y=X2, z=Z, 
        opacity=0.7, 
        colorscale='Viridis', 
        name='Function Surface',
        showscale=True,
        hovertemplate='x1: %{x:.3f}<br>x2: %{y:.3f}<br>f(x): %{z:.3f}<extra></extra>'
    ))
    
    # Add optimization path
    fig.add_trace(go.Scatter3d(
        x=path_x1, y=path_x2, z=path_z,
        mode='markers+lines',
        marker=dict(size=4, color='red', symbol='circle'),
        line=dict(color='red', width=5),
        name=f'Optimization Path ({len(history)-1} iterations)',
        hovertemplate='Iter: %{pointNumber}<br>x1: %{x:.3f}<br>x2: %{y:.3f}<br>f(x): %{z:.3f}<extra></extra>'
    ))
    
    # Add start point
    fig.add_trace(go.Scatter3d(
        x=[path_x1[0]], y=[path_x2[0]], z=[path_z[0]],
        mode='markers',
        marker=dict(size=10, color='green', symbol='square'),
        name=f'Start: ({path_x1[0]:.3f}, {path_x2[0]:.3f})',
        hovertemplate='START<br>x1: %{x:.3f}<br>x2: %{y:.3f}<br>f(x): %{z:.3f}<extra></extra>'
    ))
    
    # Add end point
    fig.add_trace(go.Scatter3d(
        x=[path_x1[-1]], y=[path_x2[-1]], z=[path_z[-1]],
        mode='markers',
        marker=dict(size=10, color='darkred', symbol='diamond'),
        name=f'End: ({path_x1[-1]:.3f}, {path_x2[-1]:.3f})',
        hovertemplate='END<br>x1: %{x:.3f}<br>x2: %{y:.3f}<br>f(x): %{z:.3f}<extra></extra>'
    ))
    
    # Update layout
    fig.update_layout(
        title=f"Interactive 3D Convergence - {oracle.__name__}<br>Step size: {step_size} | Iterations: {len(history)-1}",
        scene=dict(
            xaxis_title='x1',
            yaxis_title='x2',
            zaxis_title='f(x1, x2)',
            camera=dict(
                eye=dict(x=1.5, y=1.5, z=1.2)
            ),
            aspectmode='cube'
        ),
        width=900,
        height=700,
        showlegend=True,
        legend=dict(
            yanchor="top",
            y=0.99,
            xanchor="left",
            x=0.01
        )
    )
    
    # Display the plot
    fig.show()
    print(f"Final result: x = {x_opt}, f(x) = {path_z[-1]:.6f}, iterations = {len(history)-1}")
    
    return fig


fig_f1_1 = plot_convergence_3d_plotly(oracle_f1, x0=[-2, 2], step_size=0.05)
fig_f1_2 = plot_convergence_3d_plotly(oracle_f1, x0=[-2, 2], step_size=0.5)
fig_f1_2 = plot_convergence_3d_plotly(oracle_f1, x0=[-2, 2], step_size=0.49)
fig_f1_2 = plot_convergence_3d_plotly(oracle_f1, x0=[-2, 2], step_size=0.51)
fig_f1_3 = plot_convergence_3d_plotly(oracle_f1, x0=[-2, 2], step_size=0.005)


fig_f2_1 = plot_convergence_3d_plotly(oracle_f2, x0=[-2, 2], step_size=0.001, 
                                      max_iter=5000, x_range=(-2.5, 2.5), y_range=(-1, 5))
fig_f2_2 = plot_convergence_3d_plotly(oracle_f2, x0=[-2, 2], step_size=0.01, 
                                      max_iter=5000, x_range=(-2.5, 2.5), y_range=(-1, 5))
fig_f2_3 = plot_convergence_3d_plotly(oracle_f2, x0=[-2, 2], step_size=0.1, 
                                      max_iter=5000, x_range=(-2.5, 2.5), y_range=(-1, 5))


fig_f3_1 = plot_convergence_3d_plotly(oracle_f3, x0=[-2, 2], step_size=0.01, max_iter=1000)
fig_f3_2 = plot_convergence_3d_plotly(oracle_f3, x0=[-2, 2], step_size=0.1, max_iter=1000)
fig_f3_3 = plot_convergence_3d_plotly(oracle_f3, x0=[-2, 2], step_size=1.0, max_iter=1000)

Final result: x = [-1.68499667e-07  1.68499667e-07], f(x) = 0.000000, iterations = 74


Final result: x = [-2.  2.], f(x) = 16.000000, iterations = 1000


Final result: x = [-1.75784568e-07  1.75784568e-07], f(x) = 0.000000, iterations = 399


Final result: x = [-2.15957999e+17  2.15957999e+17], f(x) = 186551429040365226302531320697323520.000000, iterations = 1000


Final result: x = [-1.76520379e-07  1.76520379e-07], f(x) = 0.000000, iterations = 805


...

/tmp/ipykernel_35895/854703049.py:9: RuntimeWarning:

overflow encountered in scalar power

/tmp/ipykernel_35895/854703049.py:36: RuntimeWarning:

overflow encountered in scalar multiply

/home/flavien/Desktop_Windows/code mastere ose/venv/lib/python3.12/site-packages/numpy/linalg/_linalg.py:2792: RuntimeWarning:

overflow encountered in dot

/tmp/ipykernel_35895/2667886204.py:7: RuntimeWarning:

invalid value encountered in subtract



Final result: x = [nan nan], f(x) = nan, iterations = 5000


Final result: x = [-8.63424948e-05  8.63424948e-05], f(x) = 0.000000, iterations = 1000


Final result: x = [-7.0668167e-07  7.0668167e-07], f(x) = 0.000000, iterations = 142


Final result: x = [0. 0.], f(x) = 0.000000, iterations = 2


In [24]:
vecteur = -2*np.ones(10)
(x,h)= gradient_method(oracle_f3, vecteur, step_size=0.005)

In [23]:
vecteur = -2*np.ones(10000)
(x,h)= gradient_method(oracle_f3, vecteur, step_size=0.005)
print("step size 0.005:", x, "iterations:", len(h))

step size 0.005: [-0.01330794 -0.01330794 -0.01330794 ... -0.01330794 -0.01330794
 -0.01330794] iterations: 1001


### Task 3

In [ ]:
#armijo

def armijo(oracle, x0, t0=1, max_iter=100, tol=1e-6, m=0.001, theta=0.2):
    x=np.array(x0, dtype=float)
    for i in range(max_iter):
        f, g = oracle(x)
        t = t0
        while True:
            x_new = x - t * g
            f_new, _ = oracle(x_new)
            if f_new <= f - m * t * np.dot(g, g):
                break
            t *= theta
        x = x_new
        print("f", f, "x", x, "g", g, "t", t, "\n")
        if np.linalg.norm(g) < tol:
            break
    return "fini"

armijo(oracle_f2, np.array([25.0,4.0]), t0=1)

f 3856986.0 x [-14.747072   4.79488 ] g [621048. -12420.] t 6.400000000000002e-05 

f 452581.1222375602 x [-6.71580647  5.067112  ] g [-125488.52393388   -4253.62505146] t 6.400000000000002e-05 

f 16087.501493007623 x [-3.26937153  5.32333565] g [-10770.10918622   -800.69889031] t 0.00032000000000000013 

f 306.10855789673855 x [2.412271   6.18180838] g [-710.20531604 -107.30909088] t 0.008000000000000002 

f 3.31043578128886 x [2.4637561  6.17020015] g [-32.17818556   7.25513998] t 0.0016000000000000005 

f 2.242794118166516 x [2.47485684 6.16699676] g [-6.93796322  2.00212095] t 0.0016000000000000005 

f 2.192910284397523 x [2.47680244 6.16565019] g [-1.21600399  0.84160781] t 0.0016000000000000005 

f 2.1906174582271594 x [2.47782261 6.16067421] g [-0.12752129  0.62199676] t 0.008000000000000002 

f 2.188398834899397 x [2.47643477 6.15999999] g [0.86740548 0.42138605] t 0.0016000000000000005 

f 2.187296607108535 x [2.46637513 6.13818332] g [0.25149082 0.54541689] t 0.0400000000000

'fini'